In [9]:
!pip install langchain
!pip install langchain_experimental

In [15]:
from langchain.prompts.chat import (
    ChatPromptTemplate,
    HumanMessagePromptTemplate,
    MessagesPlaceholder,
)
from langchain_core.messages import SystemMessage

from langchain.chains import LLMChain
from langchain.memory import ConversationBufferMemory
from langchain_experimental.chat_models import Llama2Chat
from os.path import expanduser

from langchain_community.llms import LlamaCpp
import re

import base64
import os
from PIL import Image
from io import BytesIO
import requests
import time
import sys

In [2]:
# authentication
engine_id = "stable-diffusion-v1-6"
api_host = os.getenv('API_HOST', 'https://api.stability.ai')
api_key = "sk-dBeXPNuA8GtHabuncaZ6a7uNHnJlnaLVuaz4olhxXOf3pcOn"

In [3]:
#text to image
def text_to_image(api_key, prompt, debug=False):
    """ generates image based on text prompt and returns image data """
    try:
        response = requests.post(f"{api_host}/v1/generation/{engine_id}/text-to-image",
                                 headers={
                                     "Content-Type": "application/json",
                                     "Accept": "application/json",
                                     "Authorization": f"Bearer {api_key}"},
                                json={
                                    "text_prompts": [
                                        {"text": prompt}
                                    ],
                                    "cfg_scale": 7,
                                    "height": 576,
                                    "width": 1024,
                                    "samples": 1,
                                    "steps": 30,
                                })
        
        data = response.json()
    
        # set debug=true if debugging, will save file to local
        if debug:
            for i, image in enumerate(data["artifacts"]):
                with open(f"./txt2img_{i}.png", "wb") as f:
                    f.write(base64.b64decode(image["base64"]))
        
        image_base64 = response.json()["artifacts"][0]["base64"]  # Assuming only one image is generated
        decoded_image = base64.b64decode(image_base64)
        print(decoded_image)
        return decoded_image

    except requests.exceptions.RequestException as e:
        print(f"An error occurred: {e}")

In [4]:
# image to video
def image_to_video(api_key, img, debug=False):
    """ generates video based on image and returns video data """
    try:
        get_response = requests.post(
            f"https://api.stability.ai/v2alpha/generation/image-to-video",
            headers={"authorization": api_key},
            files={"image": img},
            data={
                "seed": 0,
                "cfg_scale": 1.8,
                "motion_bucket_id": 127
            },
        )
        
        get_response.raise_for_status()
        generation_id = get_response.json().get('id')
    
    except requests.exceptions.RequestException as e:
        print(f"An error occurred during image-to-video generation: {e}")

    try:
        status = 0
        time.sleep(5)
        while status!=200:
            time.sleep(2)
            post_response = requests.request(
            "GET",
            f"https://api.stability.ai/v2alpha/generation/image-to-video/result/{generation_id}",
            headers={
                'Accept': "video/*",  
                'authorization': api_key
            },)
            post_response.raise_for_status()
            status = post_response.status_code
        print('video Generated')
        # set debug=true if debugging, will save file to local
        if debug:
            with open("video.mp4", 'wb') as file:
                file.write(post_response.content)
                
        return post_response.content
    except requests.exceptions.RequestException as e:
        print(f"An error occurred during image-to-video result retrieval: {e}")

In [5]:
def lang_chains():
    template_message1 = [
        SystemMessage(content="You are the narrator of a dungeons and dragon game and you assist the player play the game based on the players responses, you ll ask the player to select suggested options answer"),
        MessagesPlaceholder(variable_name="chat_history"),
        HumanMessagePromptTemplate.from_template("{text}"),
    ]
    prompt_template1 = ChatPromptTemplate.from_messages(template_message1)
    template_message2 = [
        SystemMessage(content="You are the narrator of a dungeons and dragon game and assist in generating a text prompt for an image generation model for the given scenario"),
        HumanMessagePromptTemplate.from_template("{text}"),
    ]
    prompt_template2 = ChatPromptTemplate.from_messages(template_message2)
    model_path1 = "/Users/naveenrajg/Downloads/llama-2-7b-chat.Q2_K.gguf"
    model_path2 = "/Users/naveenrajg/Downloads/llama-2-7b-chat.Q2_K.gguf"

    llm1 = LlamaCpp(
        model_path=model_path1,
        streaming=False,
        n_ctx=2048,
    )
    llm2 = LlamaCpp(
        model_path=model_path2,
        streaming=False,
        n_ctx=512,
    )
    model1 = Llama2Chat(llm=llm1)
    model2 = Llama2Chat(llm=llm2)
    memory1 = ConversationBufferMemory(memory_key="chat_history", k=2, return_messages=True)
    # memory2 = ConversationBufferMemory(memory_key="prompt_history", k=2, return_messages=True)
    chain1 = LLMChain(llm=model1, prompt=prompt_template1, memory=memory1)
    chain2 = LLMChain(llm=model2, prompt=prompt_template2)
    return chain1,chain2

In [12]:
def add_prefix(text):
    return text + " . create a 10 word prompt to generate an image for this scene in format {prompt:'prompt'}"

def extract_prompt(text):
    """
    Extracts the prompt from the given text.
    
    Args:
        text (str): The input text containing the prompt.
        
    Returns:
        str: The extracted prompt, or None if no prompt is found.
    """
    # Define a regular expression pattern to match the prompt
    pattern = r'"(.*?)"'
    
    # Search for the pattern in the text
    match = re.search(pattern, text)
    
    if match:
        # If a match is found, return the prompt (group 1 of the match)
        return match.group(1)
    else:
        # If no match is found, return None
        return None

def typing_effect(text):
    for char in text:
        sys.stdout.write(char)
        sys.stdout.flush()
        time.sleep(0.05)  # Adjust the sleep time to control the typing speed
    print() 



In [7]:
def LLM_chat(text,chain1,chain2):
    image_prompt = chain2.run(
        text=add_prefix(text)
    )

    story = chain1.run(
            text=text
        )
    return image_prompt,story

In [8]:
add_prefix('A hungry Knight enters the realm of dragons')

"A hungry Knight enters the realm of dragons . create a 10 word prompt to generate an image for this scene in format {prompt:'prompt'}"

In [9]:
chain1,chain2 = lang_chains()

llama_model_loader: loaded meta data with 19 key-value pairs and 291 tensors from /Users/naveenrajg/Downloads/llama-2-7b-chat.Q2_K.gguf (version GGUF V2)
llama_model_loader: Dumping metadata keys/values. Note: KV overrides do not apply in this output.
llama_model_loader: - kv   0:                       general.architecture str              = llama
llama_model_loader: - kv   1:                               general.name str              = LLaMA v2
llama_model_loader: - kv   2:                       llama.context_length u32              = 4096
llama_model_loader: - kv   3:                     llama.embedding_length u32              = 4096
llama_model_loader: - kv   4:                          llama.block_count u32              = 32
llama_model_loader: - kv   5:                  llama.feed_forward_length u32              = 11008
llama_model_loader: - kv   6:                 llama.rope.dimension_count u32              = 128
llama_model_loader: - kv   7:                 llama.attention.head

In [10]:
image_prompt,story = LLM_chat("A hungry Knight enters the realm of dragons",chain1,chain2)
image_data = text_to_image(api_key, extract_prompt(image_prompt))
video_data = image_to_video(api_key, image_data)
print(story)


/Users/naveenrajg/Desktop/Doc/Encode/stab/lib/python3.12/site-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The function `run` was deprecated in LangChain 0.1.0 and will be removed in 0.2.0. Use invoke instead.
  warn_deprecated(

llama_print_timings:        load time =     582.86 ms
llama_print_timings:      sample time =       3.49 ms /    44 runs   (    0.08 ms per token, 12611.06 tokens per second)
llama_print_timings: prompt eval time =    5704.53 ms /    87 tokens (   65.57 ms per token,    15.25 tokens per second)
llama_print_timings:        eval time =    2912.49 ms /    43 runs   (   67.73 ms per token,    14.76 tokens per second)
llama_print_timings:       total time =    8693.01 ms /   130 tokens

llama_print_timings:        load time =     556.87 ms
llama_print_timings:      sample time =      19.57 ms /   256 runs   (    0.08 ms per token, 13082.58 tokens per second)
llama_print_timings: prompt eval time =    4590.48 ms /    71 tokens (   64

b'\x89PNG\r\n\x1a\n\x00\x00\x00\rIHDR\x00\x00\x04\x00\x00\x00\x02@\x08\x02\x00\x00\x00\x9c\xf7\x83\x82\x00\x01~\x81caBX\x00\x01~\x81jumb\x00\x00\x00\x1ejumdc2pa\x00\x11\x00\x10\x80\x00\x00\xaa\x008\x9bq\x03c2pa\x00\x00\x01~[jumb\x00\x00\x00Gjumdc2ma\x00\x11\x00\x10\x80\x00\x00\xaa\x008\x9bq\x03urn:uuid:7dea4a85-8900-4801-8f67-ac2dab3a4e67\x00\x00\x01?\xb3jumb\x00\x00\x00)jumdc2as\x00\x11\x00\x10\x80\x00\x00\xaa\x008\x9bq\x03c2pa.assertions\x00\x00\x01=Ujumb\x00\x00\x003jumd@\xcb\x0c2\xbb\x8aH\x9d\xa7\x0b*\xd6\xf4\x7fCi\x03c2pa.thumbnail.claim.jpeg\x00\x00\x00\x00\x14bfdb\x00image/jpeg\x00\x00\x01=\x06bidb\xff\xd8\xff\xe0\x00\x10JFIF\x00\x01\x02\x00\x00\x01\x00\x01\x00\x00\xff\xc0\x00\x11\x08\x02@\x04\x00\x03\x01\x11\x00\x02\x11\x01\x03\x11\x01\xff\xdb\x00C\x00\x06\x04\x05\x06\x05\x04\x06\x06\x05\x06\x07\x07\x06\x08\n\x10\n\n\t\t\n\x14\x0e\x0f\x0c\x10\x17\x14\x18\x18\x17\x14\x16\x16\x1a\x1d%\x1f\x1a\x1b#\x1c\x16\x16 , #&\')*)\x19\x1f-0-(0%()(\xff\xdb\x00C\x01\x07\x07\x07\n\x08\n\x13\n\n

In [16]:
image_prompt,story = LLM_chat("Try to find some shade and rest for a while before continuing on.",chain1,chain2)

Llama.generate: prefix-match hit

llama_print_timings:        load time =     582.86 ms
llama_print_timings:      sample time =       5.05 ms /    63 runs   (    0.08 ms per token, 12475.25 tokens per second)
llama_print_timings: prompt eval time =       0.00 ms /     1 tokens (    0.00 ms per token,      inf tokens per second)
llama_print_timings:        eval time =    4422.39 ms /    63 runs   (   70.20 ms per token,    14.25 tokens per second)
llama_print_timings:       total time =    4520.30 ms /    64 tokens
Llama.generate: prefix-match hit

llama_print_timings:        load time =     556.87 ms
llama_print_timings:      sample time =       9.81 ms /   129 runs   (    0.08 ms per token, 13143.15 tokens per second)
llama_print_timings: prompt eval time =    9342.63 ms /   144 tokens (   64.88 ms per token,    15.41 tokens per second)
llama_print_timings:        eval time =    9526.51 ms /   128 runs   (   74.43 ms per token,    13.44 tokens per second)
llama_print_timings:       to

Adventurers resting in a dark, misty forest.
b'\x89PNG\r\n\x1a\n\x00\x00\x00\rIHDR\x00\x00\x04\x00\x00\x00\x02@\x08\x02\x00\x00\x00\x9c\xf7\x83\x82\x00\x01/\xd2caBX\x00\x01/\xd2jumb\x00\x00\x00\x1ejumdc2pa\x00\x11\x00\x10\x80\x00\x00\xaa\x008\x9bq\x03c2pa\x00\x00\x01/\xacjumb\x00\x00\x00Gjumdc2ma\x00\x11\x00\x10\x80\x00\x00\xaa\x008\x9bq\x03urn:uuid:0f619526-ef23-4109-adb1-f536bcd961e1\x00\x00\x00\xf1\x04jumb\x00\x00\x00)jumdc2as\x00\x11\x00\x10\x80\x00\x00\xaa\x008\x9bq\x03c2pa.assertions\x00\x00\x00\xee\xa6jumb\x00\x00\x003jumd@\xcb\x0c2\xbb\x8aH\x9d\xa7\x0b*\xd6\xf4\x7fCi\x03c2pa.thumbnail.claim.jpeg\x00\x00\x00\x00\x14bfdb\x00image/jpeg\x00\x00\x00\xeeWbidb\xff\xd8\xff\xe0\x00\x10JFIF\x00\x01\x02\x00\x00\x01\x00\x01\x00\x00\xff\xc0\x00\x11\x08\x02@\x04\x00\x03\x01\x11\x00\x02\x11\x01\x03\x11\x01\xff\xdb\x00C\x00\x06\x04\x05\x06\x05\x04\x06\x06\x05\x06\x07\x07\x06\x08\n\x10\n\n\t\t\n\x14\x0e\x0f\x0c\x10\x17\x14\x18\x18\x17\x14\x16\x16\x1a\x1d%\x1f\x1a\x1b#\x1c\x16\x16 , #&\')*)\x19\

In [17]:
print(extract_prompt(image_prompt))
image_data = text_to_image(api_key, extract_prompt(image_prompt))
typing_effect(story)
video_data = image_to_video(api_key, image_data)
print(story)

Adventurers resting in a dark, misty forest.
b'\x89PNG\r\n\x1a\n\x00\x00\x00\rIHDR\x00\x00\x04\x00\x00\x00\x02@\x08\x02\x00\x00\x00\x9c\xf7\x83\x82\x00\x01\'\xf1caBX\x00\x01\'\xf1jumb\x00\x00\x00\x1ejumdc2pa\x00\x11\x00\x10\x80\x00\x00\xaa\x008\x9bq\x03c2pa\x00\x00\x01\'\xcbjumb\x00\x00\x00Gjumdc2ma\x00\x11\x00\x10\x80\x00\x00\xaa\x008\x9bq\x03urn:uuid:29de519d-4824-48e2-82c0-e11c03acd3d6\x00\x00\x00\xe9#jumb\x00\x00\x00)jumdc2as\x00\x11\x00\x10\x80\x00\x00\xaa\x008\x9bq\x03c2pa.assertions\x00\x00\x00\xe6\xc5jumb\x00\x00\x003jumd@\xcb\x0c2\xbb\x8aH\x9d\xa7\x0b*\xd6\xf4\x7fCi\x03c2pa.thumbnail.claim.jpeg\x00\x00\x00\x00\x14bfdb\x00image/jpeg\x00\x00\x00\xe6vbidb\xff\xd8\xff\xe0\x00\x10JFIF\x00\x01\x02\x00\x00\x01\x00\x01\x00\x00\xff\xc0\x00\x11\x08\x02@\x04\x00\x03\x01\x11\x00\x02\x11\x01\x03\x11\x01\xff\xdb\x00C\x00\x06\x04\x05\x06\x05\x04\x06\x06\x05\x06\x07\x07\x06\x08\n\x10\n\n\t\t\n\x14\x0e\x0f\x0c\x10\x17\x14\x18\x18\x17\x14\x16\x16\x1a\x1d%\x1f\x1a\x1b#\x1c\x16\x16 , #&\')*)\x19\